# Week 10 Monday

## Announcements

* I have office hours at 11am today, next door in ALP 3610.
* Videos and video quizzes due.
* Worksheets 15 and 16 due Tuesday by 11:59pm.
* There won't be a "Quiz 7".
* General plan for lectures this week: About 20 minutes lecture, then time to work on the course project.

## Don't expect conclusive results in the course project

If you're coming up with your own research question, as opposed to following a tutorial, you shouldn't expect to get conclusive (maybe not even interesting) results... that's just how research goes a lot of the time.

Today I want to use the Spotify dataset.  I think that's a great dataset for Exploratory Data Analysis (EDA).  I've tried for many hours to find an interesting Machine Learning question we can answer using this dataset (like classification: "Predict if the artist is Taylor Swift or Billie Eilish" or regression: "Predict the number of streams of a song"), but have never gotten any convincing results.

For the course project, you can decide for yourself if you'd rather investigate your own question or if you'd rather investigate someone else's question and be more confident that you will get conclusive results.  Both are good options.

## Preparing the Spotify dataset for K-means clustering

General guiding question: If we perform K-means clustering on the Spotify dataset, do songs by the same artist tend to appear in the same cluster?

The first step is to choose what columns we will use.  They need to be numeric columns and they need to not have any missing values.

In [2]:
import altair as alt
import pandas as pd
from pandas.api.types import is_numeric_dtype

Remember that missing values in this dataset are represented by a blank space `" "` (not an empty string `""` which would be fine).  Here we also drop the rows containing missing values.  Sometimes that is too drastic (like on the Titanic dataset), but here it only removes about 10 rows.

In [3]:
df = pd.read_csv("spotify_dataset.csv", na_values=" ").dropna(axis=0).copy()

Let's choose which columns (aka features, aka input variables) we want to use for our clustering.  They should all be numeric.  (If you want to use a categorical feature, first use `OneHotEncoder`.)

In [5]:
# All numeric columns
num_cols = [c for c in df.columns if is_numeric_dtype(df[c])]
num_cols

['Index',
 'Highest Charting Position',
 'Number of Times Charted',
 'Artist Followers',
 'Popularity',
 'Danceability',
 'Energy',
 'Loudness',
 'Speechiness',
 'Acousticness',
 'Liveness',
 'Tempo',
 'Duration (ms)',
 'Valence']

Let's use the columns from "Popularity" to the end.  (I don't want to use anything related too closely to the artist.)

I don't think we've used the `index` method before on a list.  Use the list method `index` to find at what index "Popularity" occurs.

In [7]:
i = num_cols.index("Popularity")
i

4

Make a list `cols` which contains the numeric column names from "Popularity" to the end.

In [8]:
cols = num_cols[i:]
cols

['Popularity',
 'Danceability',
 'Energy',
 'Loudness',
 'Speechiness',
 'Acousticness',
 'Liveness',
 'Tempo',
 'Duration (ms)',
 'Valence']

Here is a reminder of what the data in this dataset looks like.  Notice in particular how big the numbers are in the "Duration (ms)" column.  It would be a bad idea to use clustering on this dataset without scaling.

In [9]:
df.head(3)

Index  Highest Charting Position  Number of Times Charted  \
0      1                          1                        8   
1      2                          2                        3   
2      3                          1                       11   

  Week of Highest Charting                  Song Name     Streams  \
0   2021-07-23--2021-07-30                    Beggin'  48,633,449   
1   2021-07-23--2021-07-30  STAY (with Justin Bieber)  47,248,719   
2   2021-06-25--2021-07-02                   good 4 u  40,162,559   

           Artist  Artist Followers                 Song ID  \
0        Måneskin         3377762.0  3Wrjm47oTz2sjIgck11l5e   
1   The Kid LAROI         2230022.0  5HCyWlXZPP0y6Gqq8TgA20   
2  Olivia Rodrigo         6266514.0  4ZtFanR9U6ndgddUvNcjcG   

                                    Genre  ... Danceability Energy  Loudness  \
0  ['indie rock italiano', 'italian pop']  ...        0.714  0.800    -4.808   
1                  ['australian hip hop']  ...        0.591  0.764    -5.484   
2                                 ['pop']  ...        0.563  0.664    -5.044   

   Speechiness  Acousticness  Liveness    Tempo  Duration (ms)  Valence  Chord  
0       0.0504        0.1270    0.3590  134.002       211560.0    0.589      B  
1       0.0483        0.0383    0.1030  169.928       141806.0    0.478  C#/Db  
2       0.1540        0.3350    0.0849  166.928       178147.0    0.688      A  

[3 rows x 23 columns]

## K-means clustering review

We saw K-means clustering at the very beginning of the Machine Learning portion of Math 10.  (It is the only example of unsupervised learning we have discussed.)  Let's review K-means clustering.  Think about how it compares and contrasts to the supervised Machine Learning we have done (linear and polynomial regression, decision trees for classification and regression, random forests).

Remember that scaling is typically very important for K-means clustering.  If two of your columns have the same unit (like money spent on rent and money spent on food), then maybe you don't need to rescale those, but if the units for the columns are different (like money spent on rent and distance traveled to work), then I think it's essential to rescale.  (Scaling does not have any impact on decision trees, I don't think.  Scaling before linear regression can be useful or not useful depending on the context.  If you want to know which feature is the most important, I think it makes sense to rescale.  If you want to be able to interpret the precise coefficients that show up, then I don't think it makes sense to rescale.)

In [10]:
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans

Recommended exercise: try to do what we're doing below without using `Pipeline`.  I think you'll find that it involves much more typing.

In [11]:
pipe = Pipeline(
    [
        ("scaler", StandardScaler()),
        ("kmeans", KMeans(n_clusters=6))
    ]
)

Remember that we can't use all the columns, because K-means clustering requires numerical values in all the columns.

In [12]:
pipe.fit(df)

ValueError: could not convert string to float: '2021-07-23--2021-07-30'

Here we use a portion of the numeric columns.  (Eventually I want to see how songs by a single artist get divided into different clusters, so I want to remove columns like especially "Artist Followers" which will be extremely connected to the artist.)

In [13]:
pipe.fit(df[cols])

Pipeline(steps=[('scaler', StandardScaler()), ('kmeans', KMeans(n_clusters=6))])

Remember that K-means is an algorithm from unsupervised learning.  That corresponds in our `fit` call that we only gave an input `X`, not any true labels `y`.

## Most frequent artists

Which 25 artists appear most often in the dataset?  Use `value_counts`, and take advantage of the fact that by default the results are sorted.

In [14]:
df["Artist"].value_counts()

Taylor Swift               52
Lil Uzi Vert               32
Justin Bieber              32
Juice WRLD                 30
Pop Smoke                  29
                           ..
Bad Bunny, Daddy Yankee     1
Capital Bra                 1
Normani                     1
Mora, Jhay Cortez           1
José Feliciano              1
Name: Artist, Length: 712, dtype: int64

I think we used this trick once before.  We get a pandas Index (similar to a list) containing the top 25 artists.

In [15]:
top_artists = df["Artist"].value_counts().index[:25]
top_artists

Index(['Taylor Swift', 'Lil Uzi Vert', 'Justin Bieber', 'Juice WRLD',
       'Pop Smoke', 'BTS', 'Bad Bunny', 'Eminem', 'The Weeknd', 'Drake',
       'Billie Eilish', 'Ariana Grande', 'Selena Gomez', 'Doja Cat', 'J. Cole',
       'Dua Lipa', 'Tyler, The Creator', 'DaBaby', 'Lady Gaga', 'Kid Cudi',
       'Olivia Rodrigo', '21 Savage, Metro Boomin', 'Polo G', 'Mac Miller',
       'Lil Baby'],
      dtype='object')

## Making an Altair chart

I don't know if we'll have time, but let's try to make a chart like [this one from the Altair examples gallery](https://altair-viz.github.io/gallery/normalized_stacked_bar_chart.html) so we can see which artists' songs fall into which clusters.  Only use the 25 most frequently occurring artists.

Here are the last 5 rows in the DataFrame.

In [17]:
df[-5:]

Index  Highest Charting Position  Number of Times Charted  \
1551   1552                        195                        1   
1552   1553                        196                        1   
1553   1554                        197                        1   
1554   1555                        198                        1   
1555   1556                        199                        1   

     Week of Highest Charting                           Song Name    Streams  \
1551   2019-12-27--2020-01-03                           New Rules  4,630,675   
1552   2019-12-27--2020-01-03                  Cheirosa - Ao Vivo  4,623,030   
1553   2019-12-27--2020-01-03           Havana (feat. Young Thug)  4,620,876   
1554   2019-12-27--2020-01-03          Surtada - Remix Brega Funk  4,607,385   
1555   2019-12-27--2020-01-03  Lover (Remix) [feat. Shawn Mendes]  4,595,450   

                             Artist  Artist Followers                 Song ID  \
1551                       Dua Lipa        27167675.0  2ekn2ttSfGqwhhate0LSR0   
1552                 Jorge & Mateus        15019109.0  2PWjKmjyTZeDpmOUa3a5da   
1553                 Camila Cabello        22698747.0  1rfofaqEpACxVEHIZBJe6W   
1554  Dadá Boladão, Tati Zaqui, OIK          208630.0  5F8ffc8KWKNawllr5WsW0r   
1555                   Taylor Swift        42227614.0  3i9UVldZOE0aD0JnyfAZZ0   

                                                  Genre  ... Danceability  \
1551                     ['dance pop', 'pop', 'uk pop']  ...        0.762   
1552           ['sertanejo', 'sertanejo universitario']  ...        0.528   
1553  ['dance pop', 'electropop', 'pop', 'post-teen ...  ...        0.765   
1554                     ['brega funk', 'funk carioca']  ...        0.832   
1555                           ['pop', 'post-teen pop']  ...        0.448   

     Energy  Loudness  Speechiness  Acousticness  Liveness    Tempo  \
1551  0.700    -6.021       0.0694       0.00261    0.1530  116.073   
1552  0.870    -3.123       0.0851       0.24000    0.3330  152.370   
1553  0.523    -4.333       0.0300       0.18400    0.1320  104.988   
1554  0.550    -7.026       0.0587       0.24900    0.1820  154.064   
1555  0.603    -7.176       0.0640       0.43300    0.0862  205.272   

      Duration (ms)  Valence  Chord  
1551       209320.0    0.608      A  
1552       181930.0    0.714      B  
1553       217307.0    0.394      D  
1554       152784.0    0.881      F  
1555       221307.0    0.422      G  

[5 rows x 23 columns]

We will use the following Boolean Series (a pandas Series with `True` and `False` for its values) to perform Boolean indexing.  Notice for example how there is a `True` in the rows with labels 1551 and 1555.  Those artists (as we can see from the above slice) are Dua Lipa and Taylor Swift.

In [18]:
bool_ser = df["Artist"].isin(top_artists)
bool_ser

0       False
1       False
2        True
3       False
4       False
        ...  
1551     True
1552    False
1553    False
1554    False
1555     True
Name: Artist, Length: 1545, dtype: bool

Now we get the rows whose corresponding artist is among the top 25.  We also use `copy` so we can add a column to it later without any warnings showing up.

In [20]:
df_top = df[bool_ser].copy()

In [22]:
df_top["pred"] = pipe.predict(df[cols])

ValueError: Length of values (1545) does not match length of index (504)

We now add a new column to `df_top` that contains the cluster numbers.  Notice how we fit the clustering algorithm using every row in `df`, but we are only using `predict` on 504 of the rows.  It's essential to use the same columns, but there's no need to use the same rows.

In [26]:
df_top["pred"] = pipe.predict(df_top[cols])

There is now a new column on the right side, containing the cluster values.

In [24]:
df_top

Index  Highest Charting Position  Number of Times Charted  \
2         3                          1                       11   
6         7                          3                       16   
8         9                          3                        8   
10       11                          4                       43   
12       13                          5                        3   
...     ...                        ...                      ...   
1529   1530                        196                        1   
1545   1546                        128                        1   
1549   1550                        187                        1   
1551   1552                        195                        1   
1555   1556                        199                        1   

     Week of Highest Charting                             Song Name  \
2      2021-06-25--2021-07-02                              good 4 u   
6      2021-05-14--2021-05-21              Kiss Me More (feat. SZA)   
8      2021-06-18--2021-06-25                              Yonaguni   
10     2021-05-07--2021-05-14             Levitating (feat. DaBaby)   
12     2021-07-09--2021-07-16                   Permission to Dance   
...                       ...                                   ...   
1529   2020-01-10--2020-01-17                           Kinda Crazy   
1545   2019-12-27--2020-01-03                                 Candy   
1549   2019-12-27--2020-01-03  Let Me Know (I Wonder Why Freestyle)   
1551   2019-12-27--2020-01-03                             New Rules   
1555   2019-12-27--2020-01-03    Lover (Remix) [feat. Shawn Mendes]   

         Streams          Artist  Artist Followers                 Song ID  \
2     40,162,559  Olivia Rodrigo         6266514.0  4ZtFanR9U6ndgddUvNcjcG   
6     29,356,736        Doja Cat         8640063.0  748mdHapucXQri7IAO8yFK   
8     25,030,128       Bad Bunny        36142273.0  2JPLbjOn0wPCngEot2STUS   
10    23,518,010        Dua Lipa        27142474.0  463CkQjx2Zk1yXoBuierM9   
12    22,062,812             BTS        37106176.0  0LThjFY2iTtNdd4wviwVV2   
...          ...             ...               ...                     ...   
1529   4,866,777    Selena Gomez        28931149.0  59iGOjPSOcPLGl3vqEStUp   
1545   5,632,102        Doja Cat         8671649.0  1VJwtWR6z7SpZRwipI12be   
1549   4,701,532      Juice WRLD        19102888.0  3wwo0bJvDSorOpNfzEkfXx   
1551   4,630,675        Dua Lipa        27167675.0  2ekn2ttSfGqwhhate0LSR0   
1555   4,595,450    Taylor Swift        42227614.0  3i9UVldZOE0aD0JnyfAZZ0   

                                      Genre  ... Energy Loudness  Speechiness  \
2                                   ['pop']  ...  0.664   -5.044       0.1540   
6                      ['dance pop', 'pop']  ...  0.701   -3.541       0.0286   
8     ['latin', 'reggaeton', 'trap latino']  ...  0.648   -4.601       0.1180   
10           ['dance pop', 'pop', 'uk pop']  ...  0.825   -3.787       0.0601   
12             ['k-pop', 'k-pop boy group']  ...  0.741   -5.330       0.0427   
...                                     ...  ...    ...      ...          ...   
1529  ['dance pop', 'pop', 'post-teen pop']  ...  0.446  -10.304       0.0472   
1545                   ['dance pop', 'pop']  ...  0.516   -5.857       0.0444   
1549         ['chicago rap', 'melodic rap']  ...  0.537   -7.895       0.0832   
1551         ['dance pop', 'pop', 'uk pop']  ...  0.700   -6.021       0.0694   
1555               ['pop', 'post-teen pop']  ...  0.603   -7.176       0.0640   

      Acousticness  Liveness    Tempo  Duration (ms)  Valence  Chord  pred  
2          0.33500    0.0849  166.928       178147.0    0.688      A     1  
6          0.23500    0.1230  110.968       208867.0    0.742  G#/Ab     1  
8          0.27600    0.1350  179.951       206710.0    0.440  C#/Db     5  
10         0.00883    0.0674  102.977       203064.0    0.915  F#/Gb     1  
12         0.00544    0.3370  124.925       187585.0 

Here is the adaptation of the Altair code from the above link.  The `stack="normalize"` portion makes sure the total width of the chart is constant.

I don't know enough about these artists to see any clear interpretation of the results.  Notice for example how the songs by Polo G and DaBaby are almost all in the same cluster (cluster 0), whereas no songs by Kid Cudi and Lady Gaga are in that cluster.

In [25]:
alt.Chart(df_top).mark_bar().encode(
    x=alt.X('count()', stack="normalize"),
    y='Artist',
    color='pred:N'
)

alt.Chart(...)

## Aside: Idea for extra component for your course project

Random idea for an extra component for the project: use geojson data in Altair to make maps: [randomly chosen reference](https://github.com/altair-viz/altair/issues/1612#issuecomment-511830524).  Here is a more systematic reference: [UW Visualization Curriculum](https://uwdata.github.io/visualization-curriculum/altair_cartographic.html).  As far as I know, there aren't yet any geojson examples in the Altair documentation (there should be within the next few months).